In [2]:
import yfinance as yf
import pandas as pd
import openpyxl
import numpy as np
import matplotlib.pyplot as plt
from matplotlib.pyplot import figure
import statsmodels
import seaborn as sns
import scipy
from scipy import stats
from statistics import mean


import statsmodels.tsa.api as tsa
from statsmodels.graphics.tsaplots import plot_acf, plot_pacf
from statsmodels.tsa.stattools import acf, q_stat, adfuller
from scipy.stats import probplot, moment
import requests

import graphviz
import pydotplus

import eikon as ek  # the Eikon Python wrapper package
import configparser as cp

import sklearn
from sklearn import tree
from sklearn.tree import DecisionTreeClassifier
# Load libraries
from sklearn.tree import DecisionTreeClassifier # Import Decision Tree Classifier
from sklearn.model_selection import train_test_split # Import train_test_split function
from sklearn import metrics #Import scikit-learn metrics module for accuracy calculation


In [3]:
df = pd.read_csv("evaluation.csv")
df = df.dropna()
df

Unnamed: 0  ExponentialMovingAverage  WeightedMovingAverage  \
25            25                 23.388462              23.031477   
26            26                 23.273964              22.909754   
27            27                 23.092121              22.720031   
28            28                 22.918881              22.537046   
29            29                 22.732813              22.340092   
...          ...                       ...                    ...   
2801        2801                 46.282842              46.517231   
2802        2802                 46.267239              46.531046   
2803        2803                 46.342067              46.629508   
2804        2804                 46.477292              46.785908   
2805        2805                 46.606731              46.938123   

      StochasticSlow  MACDHisto        RSI  SmoothedMovingAverage       ATR  \
25         15.780879  -0.851644  35.237303              44.991152  0.868012   
26         12.558950  -0.846600  42.239855              44.716022  0.892440   
27         13.320477  -0.911975  36.193033              43.863723  0.954408   
28         17.591616  -0.958386  35.802760              43.057627  0.956665   
29         11.508232  -1.010949  33.891165              42.140981  0.921189   
...              ...        ...        ...                    ...       ...   
2801       62.745098   0.723529  57.229240              56.240661  1.258040   
2802       47.944339   0.598694  49.313460              55.547941  1.326751   
2803       42.694497   0.586601  54.917619              55.484908  1.318412   
2804       46.679317   0.639046  58.574499              55.793867  1.301383   
2805       59.835547   0.677639  58.825440              56.097025  1.256641   

            time       value  
25    2012-04-20  10000000.0  
26    2012-04-23  10000000.0  
27    2012-04-24  10000000.0  
28    2012-04-25  10000000.0  
29    2012-04-26  10000000.0  
...          ...         ...  
2801  2023-05-03  10208800.0  
2802  2023-05-04  10208800.0  
2803  2023-05-05  10208800.0  
2804  2023-05-08  10208800.0  
2805  2023-05-09  10208800.0  

[2781 rows x 10 columns]

In [4]:
price_df = pd.read_csv("data.csv")
price_df




Unnamed: 0    Datetime   Open    High     Low  Close      Volume
0              0  2012-03-15  23.00  23.500  22.700  23.40  13911300.0
1              1  2012-03-16  23.65  24.930  23.550  24.55   2063000.0
2              2  2012-03-19  24.50  25.000  24.060  24.85    974300.0
3              3  2012-03-20  24.71  25.200  24.250  24.80    444400.0
4              4  2012-03-21  24.65  25.180  24.130  24.25    782300.0
...          ...         ...    ...     ...     ...    ...         ...
2804        2804  2023-05-08  47.54  48.270  47.190  48.10    700668.0
2805        2805  2023-05-09  47.81  48.185  47.510  48.16    603175.0
2806        2806  2023-05-10  48.55  48.550  47.595  48.09    716938.0
2807        2807  2023-05-11  47.60  47.810  47.270  47.61    475617.0
2808        2808  2023-05-12  47.69  47.980  47.460  47.81    525703.0

[2809 rows x 7 columns]

In [5]:
df["Closing price"] = price_df["Close"]

In [6]:
df.columns

Index(['Unnamed: 0', 'ExponentialMovingAverage', 'WeightedMovingAverage',
       'StochasticSlow', 'MACDHisto', 'RSI', 'SmoothedMovingAverage', 'ATR',
       'time', 'value', 'Closing price'],
      dtype='object')

In [7]:
df["Short_window"] = df["Closing price"].rolling(3).mean
df["Short_window"] = df["Closing price"].rolling(3).mean

In [40]:
#df.drop(['Closing prrce'])
print(df["Closing price"])
#A function to compute a new pandas series for percentage changes of items inside a list
def pct_change(lst):
    changes = []
    for i in range(len(lst)):
        if i > 0:
            changes.append((lst[i] - lst[i-1])/lst[i-1])
        else:
            changes.append(0)

    df = pd.DataFrame(changes, index=None)
    return df

def turn_trend_into_bin(lst):
    lst = list(lst)
    bin = []
    for i in lst:
        if i > 0:
            bin.append(1)
        else:
            bin.append(-1)

    return pd.DataFrame(bin, index = None)
#changes mean
short_window = 3
long_window = 4

df["Short_window"] = pct_change(list(df["Closing price"])).rolling(short_window).mean()
df["Long_window"] = pct_change(list(df["Closing price"])).rolling(long_window).mean()
df["RSI_pct_change"] = pct_change(list(df["RSI"]))
df["WMV_pct_change"] = pct_change(list(df['WeightedMovingAverage']))

25      21.21
26      21.90
27      20.91
28      20.84
29      20.50
        ...  
2776    44.31
2777    44.59
2778    44.57
2779    45.24
2780    45.28
Name: Closing price, Length: 2756, dtype: float64


In [42]:
# df["Short_window"].plot()
# df["Long_window"].plot()

df["Short window bin"] = turn_trend_into_bin(df["Short_window"])
df["Long window bin"] = turn_trend_into_bin(df["Long_window"])
df["RSI_bin"] = turn_trend_into_bin(df["RSI_pct_change"])
df["WMV_bin"] = turn_trend_into_bin(df["WMV_pct_change"])


df = df.fillna(method="ffill")

In [43]:
#List out combinations that might help
comb_1 = ['WeightedMovingAverage', 'RSI',]
feature_cols = ['ExponentialMovingAverage', 'WeightedMovingAverage','StochasticSlow', 'MACDHisto', 'RSI', 'SmoothedMovingAverage', 'ATR']

using = ["RSI_bin", "WMV_bin"]
X = df[using].values # Features
y = df["Short window bin"].values # Target variable

# df_2 = pd.read_csv("evaluation2.csv")
# X_test = df_2[feature_cols].dropna().values
# y_test = df_2["value"].dropna().values

In [44]:
X_train, X_test, y_train, y_test = train_test_split(X, y, test_size=0.2, random_state=0)

In [45]:
# Create Decision Tree classifer object
clf = DecisionTreeClassifier()

# Train Decision Tree Classifer
clf = clf.fit(X, y)

#Predict the response for test dataset
y_pred = clf.predict(X_test)

In [46]:
print("Accuracy:",sklearn.metrics.accuracy_score(y_test, y_pred))

Accuracy: 0.6721014492753623


In [ ]:
pip install graphviz

In [38]:
from sklearn.tree import export_graphviz
from six import StringIO
from IPython.display import Image
import pydotplus

dot_data = StringIO()
export_graphviz(clf, out_file=dot_data,
                filled=True, rounded=True,
                special_characters=True,feature_names = using,class_names=None)
graph = pydotplus.graph_from_dot_data(dot_data.getvalue())
graph.write_png('diabetes.png')
Image(graph.create_png())

dot: graph is too large for cairo-renderer bitmaps. Scaling by 0.932152 to fit

dot: graph is too large for cairo-renderer bitmaps. Scaling by 0.932152 to fit

